# Overview:

This notebook computes the `class_positivity` feature

In [3]:
import numpy as np
import matplotlib.pyplot as plt
import math
import datetime as dt
import pandas as pd
import json
from sqlalchemy import create_engine
from sqlalchemy.sql import text

In [2]:
# utility functions to map between actual date and regression time index

def date_to_reg_time(date, start_date = dt.date(2021, 8, 26)):
        
    return (date - start_date).days


def reg_time_to_date(reg_time, start_date = dt.date(2021, 8, 26)):
    # for the sake of symmetry and interpretability
    
    return start_date + dt.timedelta(days = reg_time)

def string_to_date(date_str):
    if date_str is not None:
        return dt.datetime.strptime(date_str[:10], '%Y-%m-%d').date()

## First, we get data on 

* `all_student_features`: all non-class features by student-day (without the frac_class_positive covariate), including whether the student positive on that day (or whether he/she is a previous positive)
* `all_student_classes`: students and the classes they take
* `positive_students`: student positive cases with hd_notify_date between 8/26 and 12/7
* `class_schedule`: class sessions, meeting times, enrollment counts

In [3]:
all_students_classes = pd.read_csv('do_not_touch/class_registration.csv')

In [4]:
print(all_students_classes.shape)
all_students_classes.head()

(143873, 12)


employee_id_hash  is_greek  is_athlete academic_career  \
0  0x0001CEED0A3584312155FD3B695D2EB6         0           0              UG   
1  0x0001CEED0A3584312155FD3B695D2EB6         0           0              UG   
2  0x0001CEED0A3584312155FD3B695D2EB6         0           0              UG   
3  0x0001CEED0A3584312155FD3B695D2EB6         0           0              UG   
4  0x0001CEED0A3584312155FD3B695D2EB6         0           0              UG   

  academic_plan1 subject  catalog_nbr  class_number  class_enroll_tot  \
0        ESAG-BS   PLSCS       2200.0        2885.0              23.0   
1        ESAG-BS   BIOEE       4620.0       17542.0              36.0   
2        ESAG-BS    MATH       2210.0        4310.0              58.0   
3        ESAG-BS   PLSCS       2200.0        2884.0              44.0   
4        ESAG-BS   QUECH       1210.0       18873.0              11.0   

  class_section  student_infected hd_notify_date  
0           401                 0            NaN  
1             1                 0            NaN  
2             1                 0            NaN  
3             1                 0            NaN  
4           101                 0            NaN

In [6]:
all_students_features = pd.read_csv('do_not_touch/all_students_features_trunc_corrected.csv', index_col = 0) 
print(all_students_features.shape)
all_students_features.head()

C:\Users\yz685\Anaconda3\lib\site-packages\numpy\lib\arraysetops.py:569: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  mask |= (ar1 == a)


(2891563, 13)


employee_id_hash  is_greek  is_athlete academic_career  \
0  0x0001CEED0A3584312155FD3B695D2EB6         0           0              UG   
1  0x0001CEED0A3584312155FD3B695D2EB6         0           0              UG   
2  0x0001CEED0A3584312155FD3B695D2EB6         0           0              UG   
3  0x0001CEED0A3584312155FD3B695D2EB6         0           0              UG   
4  0x0001CEED0A3584312155FD3B695D2EB6         0           0              UG   

  academic_plan1 hd_notify_date     day_idx  positives_identified_on_this_day  \
0        ESAG-BS            NaN  2021-08-26                                23   
1        ESAG-BS            NaN  2021-08-27                                43   
2        ESAG-BS            NaN  2021-08-28                                57   
3        ESAG-BS            NaN  2021-08-29                                55   
4        ESAG-BS            NaN  2021-08-30                                39   

   infected_on_this_day  previous_infection  week_idx  biweek_idx  \
0                     0                   0         0           0   
1                     0                   0         0           0   
2                     0                   0         0           0   
3                     0                   0         0           0   
4                     0                   0         0           0   

   class_prevalence_on_this_day  
0                           NaN  
1                           NaN  
2                           NaN  
3                           NaN  
4                           NaN

In [7]:
all_students_features['academic_career'].value_counts()

UG      1295444
GR       899232
UG_G     255188
GM       180414
UG_A     112471
LA        96506
VM        52204
EE          104
Name: academic_career, dtype: int64

In [8]:
positive_students = pd.read_csv('do_not_touch/positive_students.csv', index_col = 0) 
print(positive_students.shape)
positive_students.head()

(714, 6)


employee_id_hash               hd_notify_date  is_greek  \
0  0xE00F3E92C639BDD0BBD99E9A13CD03F4  2021-09-09 00:00:00.0000000         1   
1  0xF195D94DD0780C71FB76CC288A59CED1  2021-09-10 00:00:00.0000000         1   
2  0x269C4236CB3ED23CF2CDDAEFE04C8295  2021-08-27 00:00:00.0000000         1   
3  0x2E5315A557040640A6FA044D6F40F5FB  2021-08-28 00:00:00.0000000         1   
4  0xEAD9251A405B52B7143EE3D12112FCF2  2021-09-02 00:00:00.0000000         1   

   is_athlete  ncaa_sport_1 academic_career  
0           0           NaN              UG  
1           0           NaN              UG  
2           0           NaN              UG  
3           0           NaN              UG  
4           0           NaN              UG

In [9]:
class_schedule = pd.read_csv('do_not_touch/class_schedule.csv', index_col = 0)
class_schedule.shape

(5631, 14)

## Generate the frac_class_positive feature

### Assumptions

* All students attend all classes they are registered for.
* Each positive person is free and infectious for a week before detection.
* For each student-day, we think of the past week as the time he/she could have caught the infection from classrooms.

### First, generate an array of class-prevalence over time.
* Initialize an empty array $P$ with columns across total_regression_time
* For each positive student $i$, confirmed on day $t_i$:
   * Let $C_i$ denote the set of classes he/she is registered for.
   * For each class $j(i)$ in $C_i$:
      * For $\tau = 1, 2, …, \min(t_i, 7)$:
         * get day of the week of $t_i-\tau$
         * if class $j(i)$ is held on this day:
            * $P[j(i), t_i - \tau]$  += 1
            
(if run into a class not in the list, add to it)

In [10]:
reg_length = len(all_students_features['day_idx'].drop_duplicates())


In [23]:
class_prevalence_columns = ['subject', 'catalog', 'section', 'enrollment', 'daily_class_hours']
class_prevalence_columns.extend([str(t) for t in np.arange(reg_length+1)])

class_positive_hours = pd.DataFrame(columns = class_prevalence_columns)
class_positive_hours

Empty DataFrame
Columns: [subject, catalog, section, enrollment, daily_class_hours, 0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, ...]
Index: []

[0 rows x 110 columns]

In [36]:
# If a class section ever had a positive, create an array for it
# if not, no need to keep an array for it

for i in range(len(positive_students)):

    emplid = positive_students['employee_id_hash'][i]
    students_classes = all_students_classes.loc[all_students_classes['employee_id_hash']==emplid].reset_index(drop=True)

    if positive_students.loc[i][['hd_notify_date']].isnull().any():
        break
    notify_date = dt.datetime.strptime(positive_students['hd_notify_date'][i][:10], '%Y-%m-%d').date()
    
    # then, map the notify date to the regression time index and day of the week
    notify_reg_time = date_to_reg_time(notify_date)
    notify_day_of_week = notify_date.isoweekday()
    
    print(emplid, 'notify date, notify date reg time', notify_date, notify_reg_time)
    
    for j in range(len(students_classes)):
        
        subject_, catalog_, section_, enrollment_ = students_classes.loc[j][
            ['subject', 'catalog_nbr', 'class_section', 'class_enroll_tot']]
        
        if students_classes.loc[j][['subject', 'catalog_nbr', 'class_section']].isnull().any():
            print('invalid class')
            continue 
        
        # locate the class and particular section the student is registered for
        class_ = class_schedule.query(
            'subject == @subject_ & catalog == @catalog_ & section == @section_ ')
        
        if len(class_)>1:
            class_ = class_.head(1)
        
        if not class_['daily_class_hours'].empty:
            daily_class_hours_ = class_['daily_class_hours'].values[0]
        else:
            daily_class_hours_ = 0.5        
            print('imputed unknown daily_class_hours with 0.5')
        
        if class_positive_hours.query('subject == @subject_ & catalog == @catalog_ & section == @section_').empty:
            
            class_positive_hours = class_positive_hours.append(
                pd.DataFrame([[subject_, catalog_, section_, enrollment_, daily_class_hours_]], 
                                 columns=['subject', 'catalog', 'section', 'enrollment', 'daily_class_hours'])
            )
        
        class_positive_hours.reset_index(drop=True, inplace = True)
        class_positive_hours.fillna(0, inplace = True)

        class_index = class_positive_hours.index[(class_positive_hours['subject']==subject_)
                                      & (class_positive_hours['catalog']==catalog_)
                                    & (class_positive_hours['section'] == section_)]        

        weekly_meeting_times = class_[['1','2','3','4','5','6','7']].reset_index(drop=True)
        
        
        if class_.empty:    
            for day_idx in range(1,6):
                weekly_meeting_times.loc[0, day_idx] = 1
            for day_idx in [6,7]:
                weekly_meeting_times.loc[0, day_idx] = 0
        
        # distribute to previous week, only to days on which the class meets
        # also log class enrollment
        
        for tau in range(min(7, notify_reg_time)):
            
            prev_reg_time = notify_reg_time - tau
            
            prev_day_of_week = (notify_day_of_week - tau) % 7
            if prev_day_of_week == 0:
                prev_day_of_week = 7
            
            if weekly_meeting_times[str(prev_day_of_week)].values[0]==1:
                
                class_positive_hours.at[class_index.values[0], str(prev_reg_time)] += 1

class_positive_hours.to_csv('0127_class_positive_hours.csv')

0xE00F3E92C639BDD0BBD99E9A13CD03F4 notify date, notify date reg time 2021-09-09 14
0xF195D94DD0780C71FB76CC288A59CED1 notify date, notify date reg time 2021-09-10 15
imputed unknown daily_class_hours with 0.5
0x269C4236CB3ED23CF2CDDAEFE04C8295 notify date, notify date reg time 2021-08-27 1
imputed unknown daily_class_hours with 0.5
0x2E5315A557040640A6FA044D6F40F5FB notify date, notify date reg time 2021-08-28 2
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0xEAD9251A405B52B7143EE3D12112FCF2 notify date, notify date reg time 2021-09-02 7
imputed unknown daily_class_hours with 0.5
0x35899507416F05B82E56E8C6D56452CC notify date, notify date reg time 2021-08-26 0
imputed unknown daily_class_hours with 0.5
0xA56D1A69A4646B3C2886A19FC09F40F7 notify date, notify date reg time 2021-10-29 64
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0xD5E86DB6A5DAAF6F2E309B7C9DC2F9E7 notify date, notify date reg time 2021-09-16

0xCED359ED75C0DC25C2DF175A5D4C0CD7 notify date, notify date reg time 2021-08-31 5
imputed unknown daily_class_hours with 0.5
0x4833AF0B665F4FA914D5DFC60F74D3E4 notify date, notify date reg time 2021-09-03 8
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0x1637CC9A5A22DF20DB2584BBE9A38EBA notify date, notify date reg time 2021-09-09 14
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0xCA80DCBC28BE23F23465CFA7AFB66DAB notify date, notify date reg time 2021-11-04 70
imputed unknown daily_class_hours with 0.5
0x6EF07B579B8C26BD24E2A162F25E2BC9 notify date, notify date reg time 2021-12-01 97
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0x5636FE6B510444EFC8CF78B04A

imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0x19ECD72A356051418D517403AF703B2C notify date, notify date reg time 2021-08-28 2
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0x797244FC22EAEF41F399A471F0DE905A notify date, notify date reg time 2021-09-21 26
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0x60667AB4D0F226830F060A85FF8A514C notify date, notify date reg time 2021-09-04 9
imputed unknown daily_class_hours with 0.5
0x6C1F03EB2B3012166ECEFB0A66A9F673 notify date, notify date reg time 2021-08-30 4
0x68605FE10311AD4D0CB634586445D043 notify date, notify date reg time 2021-12-06 102
invalid class
0x3625D265E4794BD77FCC4CB7541C1339 notify date, notify date reg time 2021-08-29 3
imputed unknown daily_class_hours with 0.5
0x5A36852144381FD5

imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0x17CE5F9F5C38991979A17D48482D6410 notify date, notify date reg time 2021-09-04 9
invalid class
0xEBA002FC5A5381910C87946D4F0D7948 notify date, notify date reg time 2021-08-31 5
imputed unknown daily_class_hours with 0.5
0xFE5FAA6891742B0E3A885007BA542566 notify date, notify date reg time 2021-08-29 3
0xE3CECE917F9C9879C1B454FA903AE89F notify date, notify date reg time 2021-08-27 1
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0xC07BECB15C63275EF90FFBBD216EA2B6 notify date, notify date reg time 2021-08-27 1
0x390CB340F17810C0FFC4E041D39DD874 notify date, notify date reg time 2021-08-28 2
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0xF82B634AB710CC94B73D65DC7FB2E49A notify date, notify date reg 

0x3E7AD4CECC059E6FC61B040AEFEEC413 notify date, notify date reg time 2021-08-28 2
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0x5186ECC0D53A326E54265F9CC1417322 notify date, notify date reg time 2021-09-01 6
0x8646CEEFAFE328040FEB1E16072DC898 notify date, notify date reg time 2021-12-02 98
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0xA4F9C6118293BEB765C26529157A9AF2 notify date, notify date reg time 2021-09-06 11
imputed unknown daily_class_hours with 0.5
0x0B5C7C728607DAA29AB3C6A4E790A7AD notify date, notify date reg time 2021-08-29 3
0xAC69F36C0AC0110B04352D5B867A894B notify date, notify date reg time 2021-08-27 1
0xFBDE3FE38EEF1474B49DF360B96AB286 notify date, notify date reg time 2021-09-24 29
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0xBF7445A7086324F67FCF73015EDD1DCF n

...

0x9AD120C80C580FD72613B5BBCD367089 notify date, notify date reg time 2021-08-30 4
0xFA5C28B8020F6AC7BF729065B2F9FF23 notify date, notify date reg time 2021-08-27 1
0xFF525E82FD160BE6B63D71BD8CB25E09 notify date, notify date reg time 2021-08-29 3
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0xD08228E6FB8B54A4B1585A9FA100DC2E notify date, notify date reg time 2021-11-24 90
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0x13A8667F5E38FF7747C346621BEBFF51 notify date, notify date reg time 2021-09-02 7
imputed unknown daily_class_hours with 0.5
0x1AF73D00AE46C04DD38CFAF4ABCF

imputed unknown daily_class_hours with 0.5
0xA32DEA0132E445F814A26E3FE854F058 notify date, notify date reg time 2021-08-29 3
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0xDBC08C3746301BB77AAF090B0410A585 notify date, notify date reg time 2021-09-09 14
0x7A96EBCA03BB3EB8ED569218A067382B notify date, notify date reg time 2021-12-03 99
imputed unknown daily_class_hours with 0.5
0xE92CC263F6401B62BEA0D2E71159A222 notify date, notify date reg time 2021-12-05 101
0x8AE994C3B487428E53FCD03D9D1BCFC4 notify date, notify date reg time 2021-08-27 1
imputed unknown daily_class_hours with 0.5
0xF91C1A5E335D9D7EABA37C03E9878E59 notify date, notify date reg time 2021-10-07 42
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_ho

imputed unknown daily_class_hours with 0.5
0x37B814C952EFBEC786D995F6691690F2 notify date, notify date reg time 2021-08-29 3
0x86D76DCB25B857842DFAC18F76E66255 notify date, notify date reg time 2021-08-31 5
0x74FB522E1CEA74D010B0A29CDCC5FF1C notify date, notify date reg time 2021-08-30 4
imputed unknown daily_class_hours with 0.5
0x0AB95E590999FAF27184FA6E77CA4451 notify date, notify date reg time 2021-11-23 89
imputed unknown daily_class_hours with 0.5
0x5E42ADE1DDE59A5A67406D925EAEBABF notify date, notify date reg time 2021-11-09 75
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0xEA64AEF74AD09558EAB1D2F279A2C904 notify date, notify date reg time 2021-09-01 6
imputed unknown daily_class_hours with 0.5
0x074AF7624E092DDED370A356BB917F41 notify date, notify date reg time 2021-08-29 3
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0x3159357E45389839C26FCFC50806D216 notify date, notify date reg time 2021-09-02 

0xD08A0A6051201577CEE0A87831611B8A notify date, notify date reg time 2021-09-02 7
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0x0B3854E4CAAC697F480D1BD964CA13F9 notify date, notify date reg time 2021-09-06 11
imputed unknown daily_class_hours with 0.5
0x6E3BEA10127975C6B344C9A34EDD72C0 notify date, notify date reg time 2021-09-22 27
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0x0E394BCD256A05AFAAC20E9962CE04FC notify date, notify date reg time 2021-10-22 57
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0x4B911A0E09F8849B4160D7DE51234DFF notify date, notify date reg tim

imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0x02F4C2EF0E5874B3A8327B1435AB64BD notify date, notify date reg time 2021-09-01 6
imputed unknown daily_class_hours with 0.5
0xEB24A505BE59304751ECCB7C336176AE notify date, notify date reg time 2021-09-04 9
0x69F54EB19F1FABD1F1B54044F561DA52 notify date, notify date reg time 2021-09-23 28
imputed unknown daily_class_hours with 0.5
0x484CCC481BE3E8EF5CB6FEA01FF5D704 notify date, notify date reg time 2021-09-08 13
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
imputed unknown daily_class_hours with 0.5
0xEE236A25DB61975C87FD2DFE32CD81B2 notify date, notify date reg time 2021-09-11 16
imputed unknown daily_class_hours with 0.5


In [37]:
class_positive_hours.head()

subject  catalog section  enrollment  daily_class_hours    0    1    2    3  \
0     BEE   1050.0     101        57.0           0.833333  0.0  0.0  0.0  0.0   
1    MATH   1910.0       1       154.0           0.833333  0.0  1.0  0.0  0.0   
2    ENGL   1167.0     106        17.0           1.250000  0.0  0.0  0.0  0.0   
3      CS   1112.0     203        35.0           0.833333  0.0  0.0  0.0  0.0   
4    CHEM   2150.0       1        77.0           0.833333  0.0  0.0  0.0  0.0   

     4  ...   95   96   97   98   99  100  101  102  103  104  
0  0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0  0.0  
1  0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
2  0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
3  0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
4  0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  

[5 rows x 110 columns]

In [38]:
class_positive_hours.shape

(1991, 110)

In [44]:
# how many classes were imputed with 0.5 hrs daily
class_positive_hours[class_positive_hours['daily_class_hours']==0.5].shape

(641, 110)

load it from saved

In [44]:
class_positive_hours = pd.read_csv('do_not_touch/class_positive_hours.csv', index_col = 0)

In [45]:
class_positive_hours

subject  catalog  section  enrollment  daily_class_hours    0    1    2  \
0        BEE   1050.0      101        57.0           0.833333  0.0  0.0  0.0   
1       MATH   1910.0        1       154.0           0.833333  0.0  1.0  0.0   
2       ENGL   1167.0      106        17.0           1.250000  0.0  0.0  0.0   
3         CS   1112.0      203        35.0           0.833333  0.0  0.0  0.0   
4       CHEM   2150.0        1        77.0           0.833333  0.0  0.0  0.0   
...      ...      ...      ...         ...                ...  ...  ...  ...   
1986   JAPAN   1101.0        1        40.0           0.833333  0.0  0.0  0.0   
1987    GOVT   6273.0      101         5.0           0.500000  0.0  0.0  0.0   
1988    HIST   1402.0      101        17.0           1.250000  0.0  0.0  0.0   
1989      NS   1600.0        1        64.0           1.250000  0.0  0.0  0.0   
1990      PE   1447.0        3        16.0           0.500000  0.0  0.0  0.0   

        3    4  ...   95   96   97   98   99  100  101  102  103  104  
0     0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0  0.0  
1     0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
2     0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
3     0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
4     0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
...   ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  
1986  0.0  1.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
1987  0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
1988  0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
1989  0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
1990  0.0  0.0  ...  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  

[1991 rows x 110 columns]

### Then, compute frac_class_pos for each student.
* Initialize an empty array $S$ of size (num_students) * (length_total_regression_time)
* For each student $i$:
   * Get $C_i$, the set of classes he/she is registered for.
   * For each day $t$:
      * $S[ i, t ] = \sum_{j \in C_i} \sum_{\tau = 1, …, min(t,7)} (\text{hour of class $j$ on day $t-\tau$}) * P[ j, t - \tau]$


In [43]:
class_positive_hours.query('subject=="PSYCH" & catalog==1101')[[str(t) for t in np.arange(reg_length)]]

0     1    2    3     4    5     6    7    8    9  ...   94   95   96  \
125  0.0  19.0  0.0  0.0  13.0  0.0  12.0  0.0  6.0  0.0  ...  0.0  1.0  0.0   

      97   98   99  100  101  102  103  
125  3.0  0.0  3.0  0.0  0.0  2.0  0.0  

[1 rows x 104 columns]

In [36]:
all_students_features.groupby(['employee_id_hash']).size().value_counts()

104    27622
3         56
4         55
7         48
2         43
       ...  
83         1
70         1
44         1
57         1
31         1
Length: 74, dtype: int64

In [11]:
all_students_classes.loc[all_students_classes['employee_id_hash']=='0x0001CEED0A3584312155FD3B695D2EB6'].reset_index(drop=True)

employee_id_hash  is_greek  is_athlete academic_career  \
0  0x0001CEED0A3584312155FD3B695D2EB6         0           0              UG   
1  0x0001CEED0A3584312155FD3B695D2EB6         0           0              UG   
2  0x0001CEED0A3584312155FD3B695D2EB6         0           0              UG   
3  0x0001CEED0A3584312155FD3B695D2EB6         0           0              UG   
4  0x0001CEED0A3584312155FD3B695D2EB6         0           0              UG   

  academic_plan1 subject  catalog_nbr  class_number  class_enroll_tot  \
0        ESAG-BS   PLSCS       2200.0        2885.0              23.0   
1        ESAG-BS   BIOEE       4620.0       17542.0              36.0   
2        ESAG-BS    MATH       2210.0        4310.0              58.0   
3        ESAG-BS   PLSCS       2200.0        2884.0              44.0   
4        ESAG-BS   QUECH       1210.0       18873.0              11.0   

  class_section  student_infected hd_notify_date  
0           401                 0            NaN  
1             1                 0            NaN  
2             1                 0            NaN  
3             1                 0            NaN  
4           101                 0            NaN

In [25]:
emplid = '0x5F877D40B1EDDE3DBC9F1DADAAC164DE'
len(all_students_features.query('employee_id_hash == @emplid'))

1

In [68]:
student_ids = all_students_features[['employee_id_hash']].drop_duplicates().reset_index(drop=True)
agg_daily_class_prevalence = pd.Series([])
agg_daily_class_prevalence_dict = {}

for i in range(len(student_ids)):
    
    is_positive = 0
    
    emplid = student_ids['employee_id_hash'][i]
    print(emplid)
    
    student_classes = all_students_classes.loc[all_students_classes['employee_id_hash']==emplid].reset_index(drop=True)
    
    student_history_length = len(all_students_features.query('employee_id_hash == @emplid'))
    print('student_history_length', student_history_length)
    agg_class_prevalence = pd.DataFrame(columns = [str(t) for t in np.arange(student_history_length)])

    # 0xDAFE5A62C2ED7146DC420A05834847CB has two hd_notify_dates, 9/1 and 12/1
    
    if str(emplid) in positive_students['employee_id_hash'].values:
        is_positive = 1
        print('this person is positive')
        hd_notify_date = min(positive_students[positive_students['employee_id_hash']==str(emplid)]['hd_notify_date'])
        hd_notify_reg_time = date_to_reg_time(string_to_date(hd_notify_date))
        print('reg time of notify date', hd_notify_reg_time)

    for j in range(len(student_classes)):
        subject_, catalog_, section_ = student_classes.loc[j][['subject', 'catalog_nbr', 'class_section']]
        if subject_ is None or catalog_ is None or section_ is None:
            continue
        
        class_positive_history = class_positive_hours.query('subject == @subject_ & catalog == @catalog_ & section == @section_')
        
        if not class_positive_history.empty:
            
            enrollment_count = class_positive_history['enrollment'].values[0]
            daily_class_hours = class_positive_history['daily_class_hours'].values[0]
            
            if is_positive == 1:
                
                if hd_notify_reg_time <= 6:
                    pre_notify_prev_history = daily_class_hours * \
                        (class_positive_history[[str(t) for t in np.arange(hd_notify_reg_time+1)]] - 1) / (enrollment_count-1)
                else:
                    pre_notify_prev_history_1 = daily_class_hours * \
                        (class_positive_history[[str(t) for t in np.arange(hd_notify_reg_time-6)]]) / (enrollment_count-1)
                    pre_notify_prev_history_2 = daily_class_hours * \
                        (class_positive_history[[str(t) for t in np.arange(hd_notify_reg_time-6, hd_notify_reg_time+1)]] - 1) / (enrollment_count-1)
                
                    pre_notify_prev_history = pd.concat([pre_notify_prev_history_1, pre_notify_prev_history_2], axis=1)

                # this is actually empty
                post_notify_prev_history = daily_class_hours * \
                    (class_positive_history[[str(t) for t in np.arange(hd_notify_reg_time+1, student_history_length)]]) / (enrollment_count-1)
                
                class_prevalence_history = pd.concat([pre_notify_prev_history, post_notify_prev_history])
                class_prevalence_history[class_prevalence_history < 0] = 0
                class_prevalence_history.replace([np.inf], 0, inplace = True)
                
            else:
                class_prevalence_history = daily_class_hours * \
                        (class_positive_history[[str(t) for t in np.arange(student_history_length)]]) / (enrollment_count-1)
                
            agg_class_prevalence = agg_class_prevalence.append(class_prevalence_history, ignore_index=True)

        
    # sum over a few previous days
    
    # first sum class positivity over rows (different classes)
    agg_sum = agg_class_prevalence.sum(axis=0).to_frame().reset_index(drop=True)

    print('agg_sum length aligns with student history length?', len(agg_sum), student_history_length, 
              len(agg_sum)==student_history_length
         )
    
    agg_sum_sliding_window = []
    for k in range(len(agg_sum)):
        agg_sum_sliding_window.append(agg_sum[max(0, k-7) : k].sum()[0])
    
    agg_sum_sliding_window = pd.Series(agg_sum_sliding_window)
    print('agg_sum_sliding_window length aligns with agg_sum length', 
          len(agg_sum_sliding_window), len(agg_sum_sliding_window) == len(agg_sum))
    
    agg_daily_class_prevalence = agg_daily_class_prevalence.append(agg_sum_sliding_window).reset_index(drop=True)
        
    agg_daily_class_prevalence_dict[emplid] = (student_history_length, len(agg_sum), len(agg_sum_sliding_window))
    

agg_daily_class_prevalence.to_csv('0129_agg_daily_class_prevalence_copy.csv')
json.dump(agg_daily_class_prevalence_dict, open('0129_agg_daily_class_prevalence_dict', 'wb'))

<ipython-input-68-258b9ed0d518>:2: DeprecationWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  agg_daily_class_prevalence = pd.Series([])


0x0001CEED0A3584312155FD3B695D2EB6
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0x0006D10D9D2AF2FA09ED007D742633B1
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0x0019A7D6C123A2907CAECA890EE78500
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0x001E81320F975882CF328BE65817DD98
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0x00201F174069EA2D6081AF34AD4DDE41
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0x0020658A202B74B0AC75B0BE3F334830
stude

agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0x00E184CE7C5479021E1524E9A226452F
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0x00E48D05014F15C487D6675F00D8CC16
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0x00E89CD144F5A59B899156152FC5C3D1
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0x00EB18D0C4A09532BFF5BC2994E5F6B5
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0x00EFB64BB3619FFDA91D32B40FECAF1C
student_history_length 104
agg_sum length aligns with student histo

agg_sum_sliding_window length aligns with agg_sum length 104 True
0x01270690CA4DADCDFB69CB2066985A55
student_history_length 28
this person is positive
reg time of notify date 27
agg_sum length aligns with student history length? 28 28 True
agg_sum_sliding_window length aligns with agg_sum length 28 True
0x01286E2B7F1BC4B7E38DDA10D14998C1
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0x01296459A06B20447166A277DC31C3DE
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0x012BFE5DADB01062361AB1E7BAE39FDC
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0x012C055B94A04E4B87ECB54DDC2268BB
student_history_length 104
agg_sum length aligns with student history length? 104 10

student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0x018912C9A28BE045E13D0C56411FCE2E
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0x018B84B770A384B90785D0CBDE32401E
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0x018D9399F845BBFA5123E0C40A351B4A
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0x018D9FD1AECF10ABEAC825FE40A25C6E
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0x018F5E2BF444AFA93871165772DB67D5
student_history_length 104
agg_sum lengt

...

0xFE843EC19C551B87D6AFA45D759268A5
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0xFE85C072F34D721830377A8BD5214FA0
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0xFE86F10C2B650D689F97E007249BACC9
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0xFE8B65113633B263802ECCFC587C9AA5
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0xFE8C0B4A7A78EAE8861255C405FDFA3B
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0xFE8C9CC4C3C8E0BC4B23FA0CDA617687
stude

student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0xFEEC693E6605C64FC0CD725C2782F11B
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0xFEF03BFE777B21C56B95AEFFEF2D9240
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0xFEF04D70AD3050541D243C76A5FB8A21
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0xFEF2F8F9FF1F6BE0F02FE447A1568F36
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0xFEF62A0BF3C3460E8871F8BA59E50DBE
student_history_length 104
agg_sum lengt

student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0xFF53F41408595FC448FD94E532E5504C
student_history_length 2
this person is positive
reg time of notify date 1
agg_sum length aligns with student history length? 2 2 True
agg_sum_sliding_window length aligns with agg_sum length 2 True
0xFF5401D5DED71DA70B0625D593846D25
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0xFF5D5218B5E5C8BDFBF224DE36D01F2C
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0xFF5EC75A80EC95A6682AB98002F6C695
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0xFF66B69DDACE26004234D9D96FCB2FE

agg_sum length aligns with student history length? 7 7 True
agg_sum_sliding_window length aligns with agg_sum length 7 True
0xFFCD49B35BF3C77648859C148EE19CE8
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0xFFCFD1F680E4C08CA2F8A454A908F9CF
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0xFFD0B12413139859679AE133E8211B5C
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0xFFD194B4BC26516A0C60C55582234CC7
student_history_length 104
agg_sum length aligns with student history length? 104 104 True
agg_sum_sliding_window length aligns with agg_sum length 104 True
0xFFD3377CA25A0CB2990812B471D306D7
student_history_length 104
agg_sum length aligns with student history len

TypeError: a bytes-like object is required, not 'str'

In [6]:
# finalized data is under do_not_touch/agg_daily_class_prevalence.csv

res = pd.read_csv('do_not_touch/agg_daily_class_prevalence.csv', index_col = 0)

C:\Users\yz685\Anaconda3\lib\site-packages\numpy\lib\arraysetops.py:569: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  mask |= (ar1 == a)


In [7]:
res

0
0        0.0
1        0.0
2        0.0
3        0.0
4        0.0
...      ...
2891558  0.0
2891559  0.0
2891560  0.0
2891561  0.0
2891562  0.0

[2891563 rows x 1 columns]